### Import Data

In [1]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from scipy.ndimage import gaussian_filter1d
from os import listdir
from os.path import isfile, join
from pandas.plotting import register_matplotlib_converters
register_matplotlib_converters()
import re
from matplotlib import cm


In [2]:
def sort_human(l):
    convert = lambda text: float(text) if text.isdigit() else text
#     alphanum = lambda key: [convert(c) for c in re.split('([-+]?[0-9]*\.?[0-9]*)', key)]
    alphanum = lambda key: [convert(c) for c in re.split('([0-9]+)', key)]
    l.sort(key=alphanum)
#     l.sort()
    return l

In [3]:
# Directory of raw data acoustic


dataDir = "Red Felser/Active acoustics/PB21/PB21_1st_cycle/" 
# dataDir = "Red Felser/Active acoustics/Correction/" 

#dataDir = "C:/Users/Evgenia/Documents/Python/active_acoustics/PB6/" 

In [4]:
def importdata(dataDir): # Input directory file
    
    onlyfiles = [f for f in listdir(dataDir) if isfile(join(dataDir, f))]  #looks for files and lists them
    datafiles1 =onlyfiles[::2] # Takes every second 
    #print(datafiles1)
    datafiles = sort_human(datafiles1) # sort list by name; check by uncomment print(datafiles) of ze op de correcte volgorde zijn
    
    parfiles = onlyfiles[1::2] # Takes every 2nd from second point (python starts counting at 0) 
#     parameters = np.zeros((len(parfiles),9))
#     print(datafiles)
#     print(parfiles)

    g = 0 
     
    for file in (datafiles):  # opens binary files
        #file = datafile[i]
        dt = np.dtype('<i2')
        f = open(dataDir+file, 'rb')
        a = np.fromfile(f, dtype=dt)

        with open(dataDir+file+".par", "r") as binary_file:  # opens par files and removes spaces in file
            par = binary_file.read()
            par=par.replace("\t", " ")
            par=par.replace("\n", " ")
            par = [float(x) for x in par.split()]

            
        ch = len(par)/8 # number of Channels
#         print(ch)
        if ch < 1: 
        
            ch = 1
            nt = int(par[1]) # number of points
            vdiv = (par[2]) # V per division
            sr = int(par[3]) # sampling rate /sec
            dt = 1/sr # time step
            off = par[4] # offset in V
            sens = par[5] # sensitivity time in sec
            delay = par[6] # delay time
            loop = [0]
            if g == 0:
                parameters = np.zeros([len(parfiles),len(loop),8])
                
            parameters[int(g),0,:] = [int(ch), nt, vdiv, sr, dt, off, sens, delay] # each parameter in parameter file
            
            
        else:
            loop = np.arange(0,int(ch))
        
#             print(loop)
    #         global nt
            if g == 0:
                parameters = np.zeros([len(parfiles),len(loop),9])
    #         print((parameters.size))

            for m in loop:
                m = int(m)
                ch = len(par)/8 # number of Channels
                nt = int(par[int(1+m*8)]) # number of points
                vdiv = (par[int(2+m*8)]) # V per division
                sr = (par[int(3+m*8)]) # sampling rate /sec
                dt = 1/sr # time step
                off = par[int(4+m*8)] # offset in V
                sens = par[int(5+m*8)] # sensitivity time in sec
                delay = par[int(6+m*8)] # delay time
                time = par[int(7+m*8)] # time
    #             print(g,m)
                parameters[int(g),m,:] = [int(ch), nt, vdiv, sr, dt, off, sens, delay, time]

        if g == 0:
            DATA = np.zeros([len(parfiles),len(loop),nt])
            FREQDATA = np.zeros((len(parfiles),len(loop),int(nt/2)-1))
#             DATA = np.zeros((len(parfiles),int(ch),nt))
#             FREQDATA = np.zeros((len(parfiles),int(ch),int(nt/2)-1))

        t = np.linspace(0,(nt-1)*dt,nt)
    #     print((t.size))
        
        data = np.zeros((int(ch),int(t.size)))
    
    
#         faxis = np.linspace(0,sr/2-sr/nt,nt/2-1)
        fft = np.zeros(int(nt))
        freqs = np.zeros((int(ch),int(nt/2)-1))
        
    
        for i in loop:   # build data file
            #print(i)
            data[int(i),:] = (a[int(i*nt):int(nt*(i+1))]*parameters[g,i,2])/3200
#             plt.figure(figsize=(20,10))
#             plt.plot(data[int(i),:])
            DATA[int(g),int(i),:] = (a[int(i*nt):int(nt*(i+1))]*parameters[g,i,2])/3200 - np.mean((a[int(i*nt):int(nt*(i+1))]*parameters[g,i,2])/3200 )
   
            fft[:] = np.abs(np.fft.fft(data[int(i),:]))
            freqs[int(i),:] =  gaussian_filter1d(fft[1:int(nt/2)], sigma=3)
            FREQDATA[int(g),int(i),:] = freqs[int(i),:]
       
        g = g + 1
    return parameters, datafiles, DATA, FREQDATA



In [5]:
parameters=importdata(dataDir)[0]
# print(parameters[3][0][4])
datafiles=importdata(dataDir)[1]
DATA=importdata(dataDir)[2]
FREQDATA=importdata(dataDir)[3]
dt = parameters[3][0][4]
sr = parameters[3][0][3]
print(dt, sr)
# dt = importdata(dataDir)[0][4]
print(len(DATA))

8e-09 125000000.0
56


In [7]:
import plotly.express as px
import plotly.graph_objects as go
a = 45

data1 = DATA[a][0]
# data2 = DATA[a+5][0]
# data3 = DATA[a+10][0]
Time_array1=np.arange(start=0, stop = len(data1)) * dt 
# Time_array2=np.arange(start=0, stop = len(data2)) * dt 


fig = go.Figure()
fig.add_trace(go.Scatter(x=Time_array1, y=data1))
# fig.add_trace(go.Scatter(x=Time_array2, y=data2))

fig.update_layout(template="simple_white", autosize=False, width=1600, height=1000, 
    xaxis_title="Time (sec)",
    yaxis_title="Amplitude (mV)",
    font=dict(
        family="New Times Roman",
        size=20,
        color="Black"))


fig.update_yaxes(showgrid=True)
fig.update_xaxes(showgrid=True)
fig.show()

# fig.write_html("Graphs/PB6/1st cycle/Full_signal.html")